In [1]:
import numpy as np
import pandas as pd

from bokeh.charts import Line, Bar, Scatter, BoxPlot
from bokeh.plotting import figure, show
from bokeh.io import output_notebook, output_file

In [2]:
repairs_2014 = pd.read_csv('data/historical-repairs-2014-merge.csv',
                           encoding="utf-8", index_col=False, parse_dates=['logged-date'])

repairs_2015 = pd.read_csv('data/historical-repairs-2015-merge.csv',
                           encoding="utf-8", index_col=False, parse_dates=['logged-date'])

repairs_2016 = pd.read_csv('data/historical-repairs-2016-mini.csv',
                           encoding="utf-8", index_col=False, parse_dates=['logged-date']) 

In [3]:
repair_costs = pd.read_csv('data/costs-historical-repairs-2014-2015-minimal.csv', 
                           encoding="utf-8", index_col=False).drop(['Property reference', 'Logged date', 
                                                                    'Trade name'], axis=1)

repair_costs = repair_costs.rename(columns={'Repair number': 'repair-number', 'Estate code': 'estate-code',
                                            'Current commitment value': 'repair-cost'})

In [4]:
#repairs_2014.head()

In [5]:
#repair_costs.head()

In [4]:
costs_2014 = pd.merge(repair_costs, repairs_2014, how='inner', left_on='repair-number', right_on='repair-number')

print len(costs_2014)

costs_2015 = pd.merge(repair_costs, repairs_2015, how='inner', left_on='repair-number', right_on='repair-number')

print len(costs_2015)

costs_2016 = pd.merge(repair_costs, repairs_2016, how='inner', left_on='repair-number', right_on='repair-number')

print len(costs_2016)

0
0
1218


In [5]:
all_repairs = pd.concat([repairs_2014, repairs_2015, repairs_2016])

In [7]:
#all_repairs.to_csv("data/repairs_data_2014_2015_2016.csv", index=False)

In [6]:
joined_df = pd.merge(repair_costs, all_repairs, how='inner', left_on='repair-number', right_on='repair-number')

In [82]:
#joined_df.head()

In [10]:
"There are costs data for {0} records out of {1} repairs.".format(len(joined_df), len(all_repairs))

'There are costs data for 1218 records out of 131750 repairs.'

In [11]:
#joined_df.to_csv("data/repairs_data_and_costs.csv", index=False)

### Look up costs over time

In [7]:
ts_costs = joined_df.drop(['repair-number', 'estate-code', 
                           'description-for-code', 'property-reference'], axis=1).groupby('logged-date').sum()

In [12]:
#ts_costs.head()

In [32]:
ts_costs_plot = figure(width=800, height=350, x_axis_type="datetime", 
                       title='Costs of repairs over time')

ts_costs_plot.line(ts_costs.index, ts_costs['repair-cost'], color='navy', line_width=2)

output_file("data/plots/costs-over-time.html")

output_notebook()

show(ts_costs_plot)

Loading BokehJS ...

### Look up number of repairs per estate

In [34]:
repairs_estate = joined_df.groupby(['estate-code'])['estate-code'].count().to_frame(name='number of repairs')

In [18]:
repairs_estate.describe()

number of repairs
count         595.000000
mean            2.047059
std             1.899265
min             1.000000
25%             1.000000
50%             1.000000
75%             2.000000
max            27.000000

#### The majority of estates seem to have only one repair in this period.

In [35]:
majority_repairs = repairs_estate[(repairs_estate['number of repairs'] >= 5)]

In [37]:
repairs_estate_plot = Bar(majority_repairs, 'index', values='number of repairs', ylabel="Number of repairs per estate",
                        xlabel="estate",
                        title="Number of repairs per estate", color='navy', width=1000)

output_notebook()

output_file("data/plots/over-5-repairs-by-estate.html")

show(repairs_estate_plot)

Loading BokehJS ...

#### Two estates have a much higher number of repairs

### Look up cost of repairs per estate

In [38]:
costs_estate = joined_df.groupby(['estate-code'])[['estate-code', 'repair-cost']].sum()

In [84]:
#costs_estate.describe()

In [39]:
majority_costs = costs_estate[(costs_estate['repair-cost'] >= 500)]

In [40]:
costs_estate_plot = Bar(majority_costs, 'index', values='repair-cost', ylabel="Cost of repairs per estate",
                        xlabel="estate",
                        title="Cost of repairs per estate (£)", color='navy', width=1000)

output_notebook()

output_file("data/plots/over-500gbp-costs-by-estate.html")

show(costs_estate_plot)

Loading BokehJS ...

#### Two estates have the most expensive repairs

### Look up the relationship between number of repairs en costs

In [85]:
#repairs_estate.head()

In [86]:
#costs_estate.head()

In [41]:
cost_vs_num = repairs_estate.join(costs_estate, how='outer')

In [13]:
cost_vs_num.head()

number of repairs  repair-cost
estate-code                                
1                            3       152.05
1041                         1        40.00
1043                         1       103.48
1051                         2        80.00
106                          1        40.00

In [42]:
print cost_vs_num['number of repairs'].corr(cost_vs_num['repair-cost'])

0.427269071577


In [43]:
cost_num_plot = Scatter(cost_vs_num, x='number of repairs', y='repair-cost', title="Number of repairs vs costs",
                        xlabel="Number of repairs", ylabel="Costs (£)", width=800)

output_file("data/plots/repair-numbers-vs-costs.html")

output_notebook()

show(cost_num_plot)

Loading BokehJS ...

In [44]:
df_drop_outliers = cost_vs_num.drop('292').drop('P217').drop('553').drop('W766')

In [45]:
print df_drop_outliers['number of repairs'].corr(df_drop_outliers['repair-cost'])

0.562883715952


In [46]:
cost_num_plot2 = Scatter(df_drop_outliers, x='number of repairs', y='repair-cost', title="Number of repairs vs costs",
                        xlabel="Number of repairs", ylabel="Costs (£)", width=800)

output_file("data/plots/repair-numbers-vs-costs-no-outliers.html")

output_notebook()

show(cost_num_plot2)

Loading BokehJS ...

### Repair costs by repair type

In [57]:
x_categories = list(joined_df['description-for-code'])
y_values = [joined_df[(joined_df['description-for-code']) == type]['repair-cost'] for type in x_categories]

print len(x_categories), len(y_values)

1218 1218


In [79]:
repair_costs_plot = BoxPlot(joined_df, values='repair-cost', label='description-for-code', color='#273359',
                            title="Repair costs grouped by repair type", plot_width=1000, #legend=True,
                            whisker_color='goldenrod', outliers=False)

#repair_costs_plot = figure(plot_width=900, plot_height=500)

#repair_costs_plot.circle(x_categories, y_values, size=6, color="green", fill_alpha=0.6)

output_file('data/plots/boxplot_costs.html')
show(repair_costs_plot)

### Sum of costs by repair type

In [87]:
#joined_df.groupby(['description-for-code'])['description-for-code', 'repair-cost'].sum()

In [47]:
sum_costs_by_type_plot = Bar(joined_df, label='description-for-code', values='repair-cost', agg='sum',
                             xlabel='Type of repair',
                             title="Sum of costs by repair type")

mean_costs_by_type_plot = Bar(joined_df, label='description-for-code', values='repair-cost', agg='mean',
                              xlabel='Type of repair', color='purple',
                              title="Mean of costs by repair type")

output_notebook()
show(sum_costs_by_type_plot)
show(mean_costs_by_type_plot)

Loading BokehJS ...